In [96]:
import os
import unicodedata
import re
import itertools
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
import gensim
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
from collections import Counter
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction import text 
from sklearn.metrics import accuracy_score, classification_report
from sklearn.decomposition import TruncatedSVD
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline
# from catboost import Pool, CatBoostClassifier #Mi portatil se piensa que la DLL es un fichero peligroso vOv no he podido probarlo
# el otro día vi que en 2019 salio y estaban hablando bastante bien, en cuanto velocidad, y comodidad tuneandolo, 
# resultados parecidos a light gbm y xgboost

In [21]:
# Reading functions:
def transmission_categories_files(main_path):
    """
    Function to read category folders
    """
    cats=[]
    try:
        cats=os.listdir(main_path)
        num_cats=len(cats)
        print("---There are {} categories to train---".format(num_cats)) if num_cats>0 else print("---There is not any category folder, add some please!")
    except ValueError:
        print("---It does not exist that path, create it or change it!")
    return cats


def files_corrector(main_path):
    """
    Function to change rare name folders
    """
    print("---Formatting file names---")
    for i_cat in cats:
        cat_path = os.path.join(main_path, i_cat)
        os.chdir(cat_path)
        txt_cat_files = os.listdir(cat_path)
        for i_file in txt_cat_files:
            if bool(re.search("^.!", i_file)):
                prev_name=re.search('^.![^!]+!', i_file).group(0)
                new_name=re.sub('\.|\!', '',prev_name)
                os.rename(i_file, new_name)
    os.chdir(main_path)
    print("DONE")
    pass


def text_to_dict(main_path, cats):
    """
    Function to put txt into a dictionary
    """
    pruebas_dict = []
    try:
        for i_cat in cats:
            print("---Loading cat {} ---".format(i_cat))
            cat_path = os.path.join(main_path, i_cat)
            os.chdir(cat_path)
            txt_cat_files = os.listdir(cat_path)
            for i_file in txt_cat_files:
                with open(i_file) as file:
                    text_data=file.readlines()
                    aux_text_dict={i_cat : text_data} #Podremos acceder a ellos a través de .keys o .values
                pruebas_dict.append(aux_text_dict)
    except ValueError:
        print("---Still with no category folders in that path. Please to continue add the data or change the path")
    os.chdir(main_path)
    return pruebas_dict

In [100]:
# Modulo lectura:
main_path="C:/Users/usuario/Desktop/Entrevistas_DS/seedtag/codetest/dataset"
cats=transmission_categories_files(main_path)
files_corrector(main_path)
data_files=text_to_dict(main_path, cats)

---There are 7 categories to train---
---Formatting file names---
DONE
---Loading cat exploration ---
---Loading cat headhunters ---
---Loading cat intelligence ---
---Loading cat logistics ---
---Loading cat politics ---
---Loading cat transportation ---
---Loading cat weapons ---


In [23]:
# Cleaning functions:
symbols_to_space = re.compile(u"[/\|\n(\; )|(\: )|( \()|(\) )|( \")|(\" )|( \')|(\' )|\t]")
symbols_to_remove = re.compile(u"[\"\'\$\€\£\(\)\:\[\]\.\,\>\<\?\-\_]")
space_repetition = re.compile(u" {2,}")
words_with_numbers = re.compile(u"\w*\d\w*")


def canonize_language(text):
    """
    Function to remove spaces, symbols...
    """
    text = strip_accents(text.strip().lower())
    text = symbols_to_space.sub(" ", text)
    text = symbols_to_remove.sub("", text)
    text = space_repetition.sub(" ", text)
    text = words_with_numbers.sub("", text)
    return text.strip()


def simple_tokenizer(text, min_token_length=0):
    """
    Function to short words
    """
    tokens = text.split(" ")
    if min_token_length > 0:
        tokens = filter(lambda x: len(x) >= min_token_length, tokens)
    return tokens


def strip_accents(input_str):
    """
    Remove accents
    """
    nfkd_form = unicodedata.normalize('NFKD', input_str)
    return nfkd_form


#lemmer = WordNetLemmatizer()

def lem_word(txt_list, lemmer):
    """
    Lemmatizer of words
    """
    return lemmer.lemmatize(txt_list, "v")

#stemmer = PorterStemmer()
def stem_word(txt_list, stemmer):
    """
    Stemmer for words
    """
    return stemmer.stem(txt_list)


def join_lines_txt(txt_list, separator=' '):
    """
    Join element words of a list into one string
    """
    return separator.join(txt_list)



In [24]:
len(data_files) # 3893 txt

3893

In [25]:
# FIRST CLEANING STEP:
# ----------------------
# Access to each text and remove "noise" like punctuation marks, spaces, symbols "\n" "\t", short words (prepositions, conjunctions),
# abreviate words in order to group/find common words related to its category. 
# We should do a cleaning that for sure has a balance between removing lot of noise (which for sure impies elimante relevant info)
# BUT keeping the core of the pattern keywords that are the clue for predicting the category
clean_data = []
n_chars = 4
stemmer = PorterStemmer()
lemmer = WordNetLemmatizer()
other_words=["@", "that", "than", "=", "*", "^", "+", "-", "these"]

#Iterate through each doc
for i_txt in np.arange(0, len(data_files)):
    txt = list(data_files[i_txt].values())[0]
    clean_txt=[]
    print("---Processing transmission {}---".format(i_txt))
    #Iterate lines of each doc and join them in one
    for i_sub_txt in np.arange(0, len(txt)):
        print("Processing line {} of transmission {}".format(i_sub_txt, i_txt))
        i_line = txt[i_sub_txt]
        txt_f1 = canonize_language(i_line)
        txt_f2 = simple_tokenizer(txt_f1, n_chars)
        txt_f2 = list(txt_f2)
        #stemmed_vector = [stem_word(element_txt, stemmer) for element_txt in txt_f2] # Stemming will go faster than lemmatizing (can be a bad idea also... if it cuts caring---> in car and not in care :O )
        #stemmed_vector=join_lines_txt(stemmed_vector)
        #clean_txt.append(stemmed_vector)
        lemmed_vector = [lem_word(element_txt, lemmer) for element_txt in txt_f2] # look up at wordnet dictionary
        lemmed_vector = [ele for ele in lemmed_vector if all(ch not in ele for ch in other_words)] #Delete words containing @ (Dont know if its good idea since i dont know if @mails correlate with the categories will be uncommented if in the analysis is not a clue)
        lemmed_vector=join_lines_txt(lemmed_vector)
        clean_txt.append(lemmed_vector)
    clean_merged_txt=join_lines_txt(clean_txt)
    # SECOND CLEANING STEP after merging:
    # ----------------------
    clean_merged_txt = clean_merged_txt.strip()
    clean_merged_txt = space_repetition.sub(" ", clean_merged_txt)
    aux_clean_data={list(data_files[i_txt].keys())[0]: clean_merged_txt }
    clean_data.append(aux_clean_data)

---Processing transmission 0---
Processing line 1 of transmission 0
Processing line 2 of transmission 0
Processing line 3 of transmission 0
Processing line 4 of transmission 0
Processing line 5 of transmission 0
Processing line 6 of transmission 0
Processing line 7 of transmission 0
Processing line 8 of transmission 0
Processing line 9 of transmission 0
Processing line 10 of transmission 0
Processing line 11 of transmission 0
Processing line 12 of transmission 0
Processing line 13 of transmission 0
Processing line 14 of transmission 0
Processing line 15 of transmission 0
Processing line 16 of transmission 0
Processing line 17 of transmission 0
Processing line 18 of transmission 0
Processing line 19 of transmission 0
Processing line 20 of transmission 0
Processing line 21 of transmission 0
Processing line 22 of transmission 0
Processing line 23 of transmission 0
Processing line 24 of transmission 0
Processing line 25 of transmission 0
Processing line 26 of transmission 0
Processing line

Processing line 123 of transmission 4
Processing line 124 of transmission 4
Processing line 125 of transmission 4
Processing line 126 of transmission 4
Processing line 127 of transmission 4
Processing line 128 of transmission 4
Processing line 129 of transmission 4
Processing line 130 of transmission 4
Processing line 131 of transmission 4
Processing line 132 of transmission 4
Processing line 133 of transmission 4
Processing line 134 of transmission 4
Processing line 135 of transmission 4
Processing line 136 of transmission 4
Processing line 137 of transmission 4
Processing line 138 of transmission 4
Processing line 139 of transmission 4
Processing line 140 of transmission 4
Processing line 141 of transmission 4
Processing line 142 of transmission 4
Processing line 143 of transmission 4
Processing line 144 of transmission 4
Processing line 145 of transmission 4
Processing line 146 of transmission 4
Processing line 147 of transmission 4
Processing line 148 of transmission 4
Processing l

Processing line 144 of transmission 7
Processing line 145 of transmission 7
Processing line 146 of transmission 7
Processing line 147 of transmission 7
Processing line 148 of transmission 7
Processing line 149 of transmission 7
Processing line 150 of transmission 7
Processing line 151 of transmission 7
Processing line 152 of transmission 7
Processing line 153 of transmission 7
Processing line 154 of transmission 7
Processing line 155 of transmission 7
Processing line 156 of transmission 7
Processing line 157 of transmission 7
Processing line 158 of transmission 7
Processing line 159 of transmission 7
Processing line 160 of transmission 7
Processing line 161 of transmission 7
Processing line 162 of transmission 7
Processing line 163 of transmission 7
Processing line 164 of transmission 7
Processing line 165 of transmission 7
Processing line 166 of transmission 7
Processing line 167 of transmission 7
Processing line 168 of transmission 7
Processing line 169 of transmission 7
Processing l

Processing line 485 of transmission 9
Processing line 486 of transmission 9
Processing line 487 of transmission 9
Processing line 488 of transmission 9
Processing line 489 of transmission 9
Processing line 490 of transmission 9
Processing line 491 of transmission 9
Processing line 492 of transmission 9
Processing line 493 of transmission 9
Processing line 494 of transmission 9
Processing line 495 of transmission 9
Processing line 496 of transmission 9
Processing line 497 of transmission 9
Processing line 498 of transmission 9
Processing line 499 of transmission 9
Processing line 500 of transmission 9
Processing line 501 of transmission 9
Processing line 502 of transmission 9
Processing line 503 of transmission 9
Processing line 504 of transmission 9
Processing line 505 of transmission 9
Processing line 506 of transmission 9
Processing line 507 of transmission 9
Processing line 508 of transmission 9
Processing line 509 of transmission 9
Processing line 510 of transmission 9
Processing l

Processing line 88 of transmission 13
Processing line 89 of transmission 13
Processing line 90 of transmission 13
Processing line 91 of transmission 13
---Processing transmission 14---
Processing line 1 of transmission 14
Processing line 2 of transmission 14
Processing line 3 of transmission 14
Processing line 4 of transmission 14
Processing line 5 of transmission 14
Processing line 6 of transmission 14
Processing line 7 of transmission 14
Processing line 8 of transmission 14
Processing line 9 of transmission 14
Processing line 10 of transmission 14
Processing line 11 of transmission 14
Processing line 12 of transmission 14
Processing line 13 of transmission 14
Processing line 14 of transmission 14
Processing line 15 of transmission 14
Processing line 16 of transmission 14
Processing line 17 of transmission 14
Processing line 18 of transmission 14
Processing line 19 of transmission 14
Processing line 20 of transmission 14
Processing line 21 of transmission 14
Processing line 22 of tran

...

Processing line 2 of transmission 3838
Processing line 3 of transmission 3838
Processing line 4 of transmission 3838
Processing line 5 of transmission 3838
Processing line 6 of transmission 3838
Processing line 7 of transmission 3838
Processing line 8 of transmission 3838
Processing line 9 of transmission 3838
Processing line 10 of transmission 3838
Processing line 11 of transmission 3838
Processing line 12 of transmission 3838
Processing line 13 of transmission 3838
Processing line 14 of transmission 3838
---Processing transmission 3839---
Processing line 1 of transmission 3839
Processing line 2 of transmission 3839
Processing line 3 of transmission 3839
Processing line 4 of transmission 3839
Processing line 5 of transmission 3839
Processing line 6 of transmission 3839
Processing line 7 of transmission 3839
Processing line 8 of transmission 3839
Processing line 9 of transmission 3839
Processing line 10 of transmission 3839
Processing line 11 of transmission 3839
Processing line 12 of 

Processing line 767 of transmission 3841
Processing line 768 of transmission 3841
Processing line 769 of transmission 3841
Processing line 770 of transmission 3841
Processing line 771 of transmission 3841
Processing line 772 of transmission 3841
Processing line 773 of transmission 3841
Processing line 774 of transmission 3841
Processing line 775 of transmission 3841
Processing line 776 of transmission 3841
Processing line 777 of transmission 3841
Processing line 778 of transmission 3841
Processing line 779 of transmission 3841
Processing line 780 of transmission 3841
Processing line 781 of transmission 3841
Processing line 782 of transmission 3841
Processing line 783 of transmission 3841
Processing line 784 of transmission 3841
Processing line 785 of transmission 3841
Processing line 786 of transmission 3841
Processing line 787 of transmission 3841
Processing line 788 of transmission 3841
Processing line 789 of transmission 3841
Processing line 790 of transmission 3841
Processing line 

Processing line 12 of transmission 3847
Processing line 13 of transmission 3847
Processing line 14 of transmission 3847
Processing line 15 of transmission 3847
Processing line 16 of transmission 3847
Processing line 17 of transmission 3847
Processing line 18 of transmission 3847
Processing line 19 of transmission 3847
Processing line 20 of transmission 3847
Processing line 21 of transmission 3847
Processing line 22 of transmission 3847
Processing line 23 of transmission 3847
Processing line 24 of transmission 3847
Processing line 25 of transmission 3847
Processing line 26 of transmission 3847
Processing line 27 of transmission 3847
Processing line 28 of transmission 3847
Processing line 29 of transmission 3847
Processing line 30 of transmission 3847
Processing line 31 of transmission 3847
Processing line 32 of transmission 3847
Processing line 33 of transmission 3847
Processing line 34 of transmission 3847
Processing line 35 of transmission 3847
Processing line 36 of transmission 3847


Processing line 11 of transmission 3864
Processing line 12 of transmission 3864
Processing line 13 of transmission 3864
Processing line 14 of transmission 3864
Processing line 15 of transmission 3864
Processing line 16 of transmission 3864
Processing line 17 of transmission 3864
Processing line 18 of transmission 3864
Processing line 19 of transmission 3864
Processing line 20 of transmission 3864
Processing line 21 of transmission 3864
Processing line 22 of transmission 3864
Processing line 23 of transmission 3864
Processing line 24 of transmission 3864
Processing line 25 of transmission 3864
---Processing transmission 3865---
Processing line 1 of transmission 3865
Processing line 2 of transmission 3865
Processing line 3 of transmission 3865
Processing line 4 of transmission 3865
Processing line 5 of transmission 3865
Processing line 6 of transmission 3865
Processing line 7 of transmission 3865
Processing line 8 of transmission 3865
Processing line 9 of transmission 3865
Processing lin

Processing line 43 of transmission 3885
Processing line 44 of transmission 3885
Processing line 45 of transmission 3885
Processing line 46 of transmission 3885
Processing line 47 of transmission 3885
Processing line 48 of transmission 3885
Processing line 49 of transmission 3885
Processing line 50 of transmission 3885
Processing line 51 of transmission 3885
Processing line 52 of transmission 3885
Processing line 53 of transmission 3885
Processing line 54 of transmission 3885
Processing line 55 of transmission 3885
Processing line 56 of transmission 3885
Processing line 57 of transmission 3885
Processing line 58 of transmission 3885
Processing line 59 of transmission 3885
Processing line 60 of transmission 3885
Processing line 61 of transmission 3885
Processing line 62 of transmission 3885
Processing line 63 of transmission 3885
Processing line 64 of transmission 3885
Processing line 65 of transmission 3885
Processing line 66 of transmission 3885
Processing line 67 of transmission 3885


In [26]:
# Conver the dictionary into a data frame to have it in another format and starting to have a closer look to a tabular data format:
# I know there is completely inneficient but the direct convertion of pd.DataFrame(clean_data) it does not help to do it in a 
# general way.
transmissions_df=pd.DataFrame()
for irow in np.arange(0, len(clean_data)):
    auxrow=clean_data[irow]
    target=list(auxrow.keys())[0]
    transmissions=list(auxrow.values())[0]
    aux_pd=pd.DataFrame([[transmissions, target]], columns=["transmissions", "target"])
    transmissions_df=transmissions_df.append(aux_pd)
transmissions_df.reset_index(inplace=True)
transmissions_df.drop(columns="index", inplace=True)
transmissions_df.head()

transmissions       target
0  constants equations calculations this list ori...  exploration
1  controversial question issue periodically come...  exploration
2  space activist interest research group space p...  exploration
3  become astronaut first short form author henry...  exploration
4  diffs since last post post order handedited co...  exploration

In [27]:
# Distribution of each category (will be balanced?)
round(transmissions_df['target'].value_counts()/sum(transmissions_df['target'].value_counts()) * 100, 2)
# Looks like the categories are balanced (or at least there is none with a 5%)

politics          15.65
transportation    15.31
headhunters       15.26
exploration       15.21
weapons           14.03
logistics         12.59
intelligence      11.95
Name: target, dtype: float64

In [28]:
# Now that we did a first cleaning step. It would be interesting to discover if there is any word/s that are really
# correlated with our topics at least to:
# 1. To understand the correlation
# 2. If we get (1.) We can do better featuring extraction to help the classifiers do better performance

# We can create a corpus to know the dimensions of our vocabulary 
# (if its big and we were thinking to build a term frequency matrix of terms and extra features will probably
# have a over dimension matrix, which means that will have to deal with it :O )

# Using sklearn we can use CountVectorize to earn in loops and create a direct matriz of counts for each category:
target="target"
var_transmissions= "transmissions"
cv = CountVectorizer(stop_words="english")
top=20
top_words=[]
for i_target in np.unique(transmissions_df[target]):
    top_dict = {}
    cat_df= transmissions_df.loc[transmissions_df[target]==i_target][var_transmissions]
    cat_df=pd.DataFrame(cat_df, columns=[var_transmissions])
    cat_cv = cv.fit_transform(cat_df[var_transmissions])
    cat_dtm = pd.DataFrame(cat_cv.toarray(), columns=cv.get_feature_names()) 
    cat_dtm_T = cat_dtm.transpose()
    cat_dtm_T["Total_Count_Words_In_Category"] = cat_dtm_T.sum(axis=1)
    top_cat_df = cat_dtm_T["Total_Count_Words_In_Category"].sort_values(ascending=False).head(top)
    top_dict[i_target]= list(zip(top_cat_df.index, top_cat_df.values))
    print("\n\nFor the category {} those are the top {} most used words".format(i_target, top))
    print(".----.")
    print(top_dict)
    top_words.append(top_cat_df.index)



For the category exploration those are the top 20 most used words
.----.
{'exploration': [('space', 996), ('write', 513), ('launch', 454), ('article', 396), ('nasa', 377), ('like', 340), ('just', 336), ('orbit', 300), ('time', 299), ('satellite', 293), ('think', 288), ('make', 284), ('know', 279), ('work', 258), ('earth', 247), ('moon', 240), ('use', 237), ('data', 228), ('program', 227), ('cost', 210)]}


For the category headhunters those are the top 20 most used words
.----.
{'headhunters': [('image', 760), ('file', 527), ('write', 470), ('graphics', 433), ('program', 382), ('use', 318), ('know', 290), ('format', 265), ('jpeg', 254), ('article', 240), ('color', 236), ('software', 230), ('data', 230), ('look', 227), ('point', 224), ('need', 222), ('like', 221), ('email', 212), ('package', 203), ('line', 197)]}


For the category intelligence those are the top 20 most used words
.----.
{'intelligence': [('write', 685), ('people', 681), ('make', 590), ('think', 579), ('article', 573)

In [29]:
####################################################################################################################
# Observations: Words that coul be related with each category:
# exploration: 'earth', 'moon','orbit', 'time', 'work'
# headhunters: 'file', 'graphics', 'program'
# intelligence: 'president', 'goverment'
# politcs: 'game', 'season'
# transportation: 'speed', 'engine', 'drive'
# weapons: 'weapons', 'firearms', 'kill'
####################################################################################################################


# Looking at the top most common words, they are repetead among the categories, probably a good idea would be exclude them
# due they dont are very discriminant. 
add_stop_words =list(set(top_words[0]) & set(top_words[1]) & 
                     set(top_words[2]) &  set(top_words[3]) & 
                     set(top_words[4]) & set(top_words[5]) & 
                     set(top_words[6]))
print(add_stop_words)

['write', 'like', 'article', 'know']


In [31]:
# Also as low contribution for the prediction can be when a world only has a very low of repetitions:
rep = 5 #seven the number of the good luck
target = "target"
var_transmissions= "transmissions"
cv = CountVectorizer(stop_words="english")

bottom_words=[]
for i_target in np.unique(transmissions_df[target]):
    top_dict = {}
    cat_df= transmissions_df.loc[transmissions_df[target]==i_target][var_transmissions]
    cat_df=pd.DataFrame(cat_df, columns=[var_transmissions])
    cat_cv = cv.fit_transform(cat_df[var_transmissions])
    cat_dtm = pd.DataFrame(cat_cv.toarray(), columns=cv.get_feature_names()) 
    cat_dtm_T = cat_dtm.transpose()
    cat_dtm_T["Total_Count_Words_In_Category"] = cat_dtm_T.sum(axis=1)
    cat_dtm_T=cat_dtm_T.loc[cat_dtm_T["Total_Count_Words_In_Category"] < rep]
    top_cat_df = cat_dtm_T["Total_Count_Words_In_Category"].sort_values(ascending=False)
    top_dict[i_target]= list(zip(top_cat_df.index, top_cat_df.values))
    print("\n\nFor the category {} those are the words with low frecuency <{}".format(i_target, rep))
    print(".----.")
    print(top_dict)
    bottom_words.append(top_cat_df.index)
    
bottom_words_flatten = list(itertools.chain.from_iterable(bottom_words))



For the category exploration those are the words with low frecuency <5
.----.
{'exploration': [('match', 4), ('interpretation', 4), ('fish', 4), ('nuetron', 4), ('seds', 4), ('apogee', 4), ('interface', 4), ('firsteps', 4), ('campus', 4), ('apparatus', 4), ('semimajor', 4), ('invent', 4), ('intervals', 4), ('norman', 4), ('nope', 4), ('intrigue', 4), ('sensitivity', 4), ('desk', 4), ('noon', 4), ('turnaround', 4), ('canyon', 4), ('intellectual', 4), ('integrate', 4), ('intact', 4), ('schaefer', 4), ('inspector', 4), ('instability', 4), ('underwater', 4), ('obviously', 4), ('scope', 4), ('antennae', 4), ('carlos', 4), ('cargo', 4), ('demonstration', 4), ('flare', 4), ('carefully', 4), ('uncorrected', 4), ('instrumentation', 4), ('obnoxious', 4), ('demonstrator', 4), ('captain', 4), ('separately', 4), ('caliber', 4), ('offline', 4), ('tremendous', 4), ('shell', 4), ('diameters', 4), ('busy', 4), ('tricky', 4), ('bussard', 4), ('shit', 4), ('jerry', 4), ('triad', 4), ('niederstrasser', 



For the category intelligence those are the words with low frecuency <5
.----.
{'intelligence': [('latin', 4), ('calculations', 4), ('rubber', 4), ('dfens', 4), ('caffeine', 4), ('movements', 4), ('traditionally', 4), ('motivations', 4), ('sachs', 4), ('expend', 4), ('dialysis', 4), ('inevitably', 4), ('sacrifice', 4), ('bureaucrats', 4), ('inflate', 4), ('bureaucracy', 4), ('inflation', 4), ('torpedo', 4), ('salary', 4), ('devise', 4), ('routinely', 4), ('execution', 4), ('route', 4), ('trip', 4), ('extensive', 4), ('antibolshevik', 4), ('myopic', 4), ('destruction', 4), ('roadblocks', 4), ('incidents', 4), ('rob', 4), ('incomes', 4), ('calvin', 4), ('murphy', 4), ('antipodes', 4), ('rope', 4), ('ross', 4), ('expression', 4), ('roughly', 4), ('antitrust', 4), ('infrastructure', 4), ('application', 4), ('microsoft', 4), ('arguable', 4), ('minor', 4), ('estate', 4), ('establishment', 4), ('miniskirt', 4), ('seal', 4), ('brilliant', 4), ('espouse', 4), ('milwaukee', 4), ('escape', 4), 



For the category logistics those are the words with low frecuency <5
.----.
{'logistics': [('religous', 4), ('pole', 4), ('television', 4), ('corner', 4), ('telephone', 4), ('copeland', 4), ('atrocious', 4), ('atrocities', 4), ('attach', 4), ('plain', 4), ('plainly', 4), ('teachers', 4), ('teacher', 4), ('henling', 4), ('plant', 4), ('plat', 4), ('attractive', 4), ('cooper', 4), ('cool', 4), ('heretic', 4), ('convict', 4), ('temporarily', 4), ('phone', 4), ('heinlein', 4), ('persevere', 4), ('coutesy', 4), ('perceptions', 4), ('expectations', 4), ('asimov', 4), ('theories', 4), ('intron', 4), ('assassinate', 4), ('assault', 4), ('theirs', 4), ('franklin', 4), ('persuasive', 4), ('pertain', 4), ('perversion', 4), ('intrinsically', 4), ('experimental', 4), ('pharisees', 4), ('expert', 4), ('tenth', 4), ('talkorigins', 4), ('herring', 4), ('crack', 4), ('tablets', 4), ('bacteria', 4), ('pregnancy', 4), ('congressional', 4), ('prescribe', 4), ('bahavior', 4), ('supplement', 4), ('presuma



For the category transportation those are the words with low frecuency <5
.----.
{'transportation': [('aarm', 4), ('armor', 4), ('camaros', 4), ('shaky', 4), ('shake', 4), ('nextmail', 4), ('server', 4), ('sequence', 4), ('capri', 4), ('desoto', 4), ('seniors', 4), ('semi', 4), ('firebird', 4), ('noon', 4), ('northbound', 4), ('norway', 4), ('unhappy', 4), ('deserve', 4), ('carjack', 4), ('intent', 4), ('sedate', 4), ('security', 4), ('securely', 4), ('secondhand', 4), ('department', 4), ('object', 4), ('installations', 4), ('inspection', 4), ('flashers', 4), ('innocent', 4), ('tuesday', 4), ('sharp', 4), ('newest', 4), ('fewer', 4), ('trash', 4), ('jammers', 4), ('dipstick', 4), ('bury', 4), ('treat', 4), ('sides', 4), ('nation', 4), ('assure', 4), ('fee', 4), ('naturally', 4), ('buzz', 4), ('trevor', 4), ('dilute', 4), ('fellow', 4), ('shos', 4), ('trigger', 4), ('negative', 4), ('female', 4), ('neighborhood', 4), ('neilson', 4), ('shine', 4), ('diesels', 4), ('neumann', 4), ('neut



For the category weapons those are the words with low frecuency <5
.----.
{'weapons': [('cosmos', 4), ('surface', 4), ('suppress', 4), ('evaluate', 4), ('european', 4), ('ethnic', 4), ('billions', 4), ('binary', 4), ('eternal', 4), ('suit', 4), ('madmen', 4), ('suddenly', 4), ('sudden', 4), ('successfully', 4), ('succeed', 4), ('erik', 4), ('substitute', 4), ('blackman', 4), ('subsequent', 4), ('manufacturers', 4), ('maryland', 4), ('evelyn', 4), ('lone', 4), ('lever', 4), ('surround', 4), ('teeth', 4), ('technologically', 4), ('techniques', 4), ('battlefield', 4), ('expand', 4), ('teacher', 4), ('existance', 4), ('limbaugh', 4), ('tap', 4), ('befor', 4), ('tale', 4), ('exclusively', 4), ('belch', 4), ('liveslost', 4), ('beliefs', 4), ('exchange', 4), ('lloyd', 4), ('exceed', 4), ('login', 4), ('blvd', 4), ('enumerate', 4), ('mateo', 4), ('enuff', 4), ('empire', 4), ('spokesperson', 4), ('spill', 4), ('misunderstand', 4), ('electronic', 4), ('spanishamerican', 4), ('elect', 4), ('ein

In [32]:
# Randomize data set / its been created in an ordinal way:
transmissions_df = transmissions_df.reindex(np.random.permutation(transmissions_df.index)).reset_index(drop=True)

In [33]:
#Add to the common words
words_to_remove=[add_stop_words, bottom_words_flatten]
words_to_remove=list(itertools.chain.from_iterable(words_to_remove))

stop_words = text.ENGLISH_STOP_WORDS.union(words_to_remove)
# Now we are aviable to fix the matrix and save it.

In [34]:
# Approach model 1:
# Split randomly 80/20 ( cross validation also is a good idea to be sure that randomly we  )
x_train, x_test, y_train, y_test = train_test_split(transmissions_df.transmissions, 
                                                    transmissions_df.target, 
                                                    test_size=0.2, 
                                                    random_state=12358)

print("Train shape: ", x_train.shape)
print("Test shape: ", x_test.shape)

# Will use a term frequency–inverse document frequency matrix, will use this statistic to predict the target. Conceptually
# we assume that the low frecuency words that are not noise, will be somwhow shadowed by the great frecuencies. This statistcs
# can counter this effect:
tfidf = TfidfVectorizer(ngram_range=(1,1), stop_words=stop_words)
svd = TruncatedSVD(100) # Nos quedamos con las 50 mas relevantes

Train shape:  (3113,)
Test shape:  (779,)


In [633]:
# Random forest (bagging technic)
rf_clf = RandomForestClassifier(n_estimators=1500, class_weight="balanced", max_depth=8, random_state=655321)
#Never seen better performance after 1500 trees.
pipe = Pipeline([("tfidf", tfidf), ("svd", svd), ("clf", rf_clf)])
model = pipe.fit(x_train, y_train)
# Results
print("=============== Results Training set ===============")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_train), y_train)))
print(classification_report(model.predict(x_train), y_train))
print("===================================================")
print("\n -- \t -- \t -- \t -- \t -- \t -- \t --\n")
print("================= Results Test set ================")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_test), y_test)))
print(classification_report(model.predict(x_test), y_test))
print("===================================================")

=============== Results Training set ===============
Accuracy: 0.911660777385159

                precision    recall  f1-score   support

   exploration       0.91      0.92      0.91       468
   headhunters       0.92      0.90      0.91       496
  intelligence       0.91      0.94      0.93       357
     logistics       0.96      0.85      0.90       434
      politics       0.90      0.94      0.92       460
transportation       0.89      0.91      0.90       467
       weapons       0.89      0.93      0.91       431

      accuracy                           0.91      3113
     macro avg       0.91      0.91      0.91      3113
  weighted avg       0.91      0.91      0.91      3113


 -- 	 -- 	 -- 	 -- 	 -- 	 -- 	 --

================= Results Test set ================
Accuracy: 0.7086007702182285

                precision    recall  f1-score   support

   exploration       0.68      0.70      0.69       117
   headhunters       0.83      0.62      0.71       144
  intelligen

In [639]:
# Gradient boosting trees (cumulative error optimization to compare with bagging)
xgb_clf= XGBClassifier(max_depth=5, n_estimators=1000, learning_rate=0.01)
pipe = Pipeline([("tfidf", tfidf), ("svd", svd), ("clf", xgb_clf)])
model = pipe.fit(x_train, y_train)
# Results
print("=============== Results Training set ===============")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_train), y_train)))
print(classification_report(model.predict(x_train), y_train))
print("===================================================")
print("\n -- \t -- \t -- \t -- \t -- \t -- \t --\n")
print("================= Results Test set ================")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_test), y_test)))
print(classification_report(model.predict(x_test), y_test))
print("===================================================")

=============== Results Training set ===============
Accuracy: 0.9948602634115001

                precision    recall  f1-score   support

   exploration       1.00      1.00      1.00       472
   headhunters       1.00      0.98      0.99       495
  intelligence       0.99      1.00      1.00       367
     logistics       1.00      1.00      1.00       383
      politics       0.99      1.00      0.99       475
transportation       1.00      1.00      1.00       476
       weapons       1.00      1.00      1.00       445

      accuracy                           0.99      3113
     macro avg       0.99      1.00      1.00      3113
  weighted avg       0.99      0.99      0.99      3113


 -- 	 -- 	 -- 	 -- 	 -- 	 -- 	 --

================= Results Test set ================
Accuracy: 0.7650834403080873

                precision    recall  f1-score   support

   exploration       0.74      0.77      0.76       115
   headhunters       0.85      0.67      0.75       138
  intellige

In [35]:
#### COMMENTS:
# We test two models of different philosophies, since XGBoost(light gbm or catboost) are the reference 
# and for this chellenge proposes wont be test it more algorithms (logistic could be interesting as a basic benchmark, 
# support vector machine actually it looks that always appear but never happen that I got a good result with it so I dont like it a lot...)

# In terms of hyperparametrization:
# After testing second and third approach will pick best performance model looking at precision and recall in order to pay
# attention on the real true positive ratios.
# Since the data is balance, its also good to look at the overall accuracy.

#About xgboost: always as light gbm, is a must model to test, in order to build the end to end skeleton of your project quick fast, before start optimizing.
#About random forest, still good if there are not tones of data... otherwise it could take more than two days training. (in R theres is the ranger library a fast implemetation of random forest)

In [37]:
# Approach model 2: Using Word2Vec substract avg information of eahc row (weighted embedding mean of each doc) and use those
# 300 dimensional variables as predictors:
# The assumptio here, if there is a good cleaning process, there should be a bag of words enough big to represent each category
# this words can be looked up at word2vec model.
# So each doc has a bag of embeddings (one for each word), then they can be weight averaged and if everything goes well
# each tranmission should have its own embedding of 300 elements/predictors 

def annotation_weight_representation(venue_annotation):
    """
    Function that iterates a long a list vocab. Look up for its embedding. Make weighted avg of embeddings 
    """
    venue_vectors = []
    count_model_included = 0
    count_model_nonincluded = 0
    idx_token_vectors = 0
    
    tags = venue_annotation.split()
    word_vectors = np.empty(shape=(len(tags), 300))
    idx_word_vectors = 0
    for tag in tags:
        tag = tag.replace('_', ' ')
        if tag in model.vocab:
            word_vectors[idx_word_vectors] = model[tag]
            idx_word_vectors += 1
        else:
            tokens = tag.split()
            token_vectors = np.empty(shape=(len(tokens), 300))
            idx_token_vectors = 0
            for token in tokens:
                if token in model.vocab:
                    token_vectors[idx_token_vectors] = model[token]
                    idx_token_vectors += 1
                else:
                    continue
            if idx_token_vectors > 0:
                word_vectors[idx_word_vectors] = np.average(token_vectors[:idx_token_vectors], axis=0)
                idx_word_vectors += 1
    
    if idx_word_vectors != 0 or idx_token_vectors != 0:
        count_model_included += 1
        venue_vectors.append(np.average(word_vectors[:idx_word_vectors], axis=0))
    else:
        count_model_nonincluded += 1
        venue_vectors.append(np.nan)

    return venue_vectors[0]

In [45]:
#Load the w2vec model:
model=gensim.models.KeyedVectors.load_word2vec_format(os.path.join(main_path, "C:/Users/usuario/Desktop/Entrevistas_DS/seedtag/GoogleNews-vectors-negative300.bin") ,binary=True)
# We apply by row the above function in order to convert each tranmission in an embedding (hopefully could it be representative)
transmissions_df["vector_rep"] = transmissions_df["transmissions"].apply(lambda x: annotation_weight_representation(x)) #it takes couple of GB of RAM

In [52]:
# Expand the elements embedding as variables and stick the target variable to have our master table:
embeddings_df = transmissions_df['vector_rep'].apply(pd.Series)
embeddings_df = embeddings_df.rename(columns = lambda x : 'element_' + str(x))
embeddings_df = pd.merge(embeddings_df, transmissions_df["target"], left_index=True, right_index=True)
embeddings_df.head()

element_0  element_1  element_2  element_3  element_4  element_5  \
0  -0.054379  -0.024378   0.024823   0.099642  -0.105782   0.026726   
1   0.018562   0.010427   0.033731   0.124980  -0.051487  -0.002370   
2   0.009068  -0.006378  -0.012907   0.121460  -0.097889   0.019855   
3   0.024424   0.034549   0.003070   0.084747  -0.038133  -0.018763   
4   0.028813  -0.021576   0.039198   0.086897  -0.051791   0.028833   

   element_6  element_7  element_8  element_9  ...  element_291  element_292  \
0   0.037129  -0.127835   0.066525   0.042122  ...     0.064182    -0.062267   
1   0.081325  -0.017632   0.076403   0.036418  ...     0.031843    -0.078396   
2   0.115952  -0.005348   0.012696   0.017069  ...     0.064092     0.009322   
3   0.010766  -0.093231   0.077696   0.085075  ...     0.036429    -0.078548   
4   0.041217  -0.070785   0.040558   0.070053  ...     0.061297    -0.040565   

   element_293  element_294  element_295  element_296  element_297  \
0     0.049754    -0.031810    -0.034280     0.019237    -0.076733   
1    -0.012866     0.017287    -0.049327    -0.037746    -0.070023   
2     0.034668    -0.033950    -0.029179     0.060308    -0.064852   
3    -0.001959    -0.040592    -0.004239     0.013982    -0.069440   
4     0.018512     0.001669    -0.014651    -0.017057    -0.068705   

   element_298  element_299       target  
0     0.011137    -0.041329      weapons  
1     0.039534    -0.065320  exploration  
2     0.019745    -0.003286  headhunters  
3     0.047499    -0.029397     politics  
4    -0.018046    -0.047472  headhunters  

[5 rows x 301 columns]

In [92]:
# Once we got the vector representation we could do the same as above to compare if the models used in approach 1, have a better 
# performance
# Split randomly 80/20

sz = embeddings_df.shape
train = embeddings_df.iloc[:int(sz[0] * 0.8), :]
test = embeddings_df.iloc[int(sz[0] * 0.8):, :]
train=train.dropna()
test=test.dropna()

# Save the train and test data sets with its label
x_train = train.iloc[:, :300]
y_train = train.iloc[:, 300]

x_test = test.iloc[:, :300]
y_test = test.iloc[:, 300]

print("Train shape: ", x_train.shape)
print("Test shape: ", x_test.shape)


Train shape:  (3107, 300)
Test shape:  (778, 300)


In [94]:
# Random forest (bagging technic)
rf_clf = RandomForestClassifier(n_estimators=1500, class_weight="balanced", max_depth=5, random_state=655321)
model = rf_clf.fit(x_train, y_train)
# Results
print("=============== Results Training set ===============")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_train), y_train)))
print(classification_report(model.predict(x_train), y_train))
print("===================================================")
print("\n -- \t -- \t -- \t -- \t -- \t -- \t --\n")
print("================= Results Test set ================")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_test), y_test)))
print(classification_report(model.predict(x_test), y_test))
print("===================================================")

=============== Results Training set ===============
Accuracy: 0.8764081107177342

                precision    recall  f1-score   support

   exploration       0.86      0.94      0.90       430
   headhunters       0.96      0.86      0.91       518
  intelligence       0.78      0.82      0.80       348
     logistics       0.87      0.82      0.85       417
      politics       0.96      0.91      0.94       513
transportation       0.85      0.94      0.89       441
       weapons       0.83      0.82      0.83       440

      accuracy                           0.88      3107
     macro avg       0.87      0.87      0.87      3107
  weighted avg       0.88      0.88      0.88      3107


 -- 	 -- 	 -- 	 -- 	 -- 	 -- 	 --

================= Results Test set ================
Accuracy: 0.8046272493573264

                precision    recall  f1-score   support

   exploration       0.76      0.88      0.81       107
   headhunters       0.90      0.82      0.85       137
  intellige

In [95]:
# Xgboost (with less estimators and depht to avoid overfitting):
xgb_clf= XGBClassifier(max_depth=4, n_estimators=300, learning_rate= 0.01)
model = xgb_clf.fit(x_train, y_train)
# Results
print("=============== Results Training set ===============")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_train), y_train)))
print(classification_report(model.predict(x_train), y_train))
print("===================================================")
print("\n -- \t -- \t -- \t -- \t -- \t -- \t --\n")
print("================= Results Test set ================")
print("Accuracy: {}\n".format(accuracy_score(model.predict(x_test), y_test)))
print(classification_report(model.predict(x_test), y_test))
print("===================================================")

=============== Results Training set ===============
Accuracy: 0.9633086578693273

                precision    recall  f1-score   support

   exploration       0.95      0.98      0.97       456
   headhunters       0.99      0.97      0.98       474
  intelligence       0.93      0.93      0.93       367
     logistics       0.95      0.94      0.94       401
      politics       0.99      0.99      0.99       492
transportation       0.95      0.99      0.97       468
       weapons       0.97      0.94      0.95       449

      accuracy                           0.96      3107
     macro avg       0.96      0.96      0.96      3107
  weighted avg       0.96      0.96      0.96      3107


 -- 	 -- 	 -- 	 -- 	 -- 	 -- 	 --

================= Results Test set ================
Accuracy: 0.8071979434447301

                precision    recall  f1-score   support

   exploration       0.79      0.85      0.82       115
   headhunters       0.90      0.87      0.89       130
  intellige

In [90]:
#NOTE: COULD BE INTERESTING TO TRY THE FASTAI SEE WHETHER THERE IS ANY BENEFIT OF USING TRANSFER LEARNING  
#ALTHOUGH IN APPROACH 2 WE DID A PSEUDO TRANSFER LEARNING. WE TOOK THE WEIGHTS/EMBEDDINGS OF THOSE WORDS.

In [ ]:
# AFTER THIS WE DECIDE TO USE THE SECOND APPROACH USING :
# To be practical we implement random forest for the solution:
# 1. They have similar results (the train looks less overfitted than xgboost)
# 2. More stable than xgboost hyperparametrization
# (Its true that they should have a little hyperparameter tuning)